In [3]:
pip install pandas

Defaulting to user installation because normal site-packages is not writeable
     |████████████████████████████████| 12.3 MB 7.3 MB/s            
     |████████████████████████████████| 341 kB 132.3 MB/s            
Note: you may need to restart the kernel to use updated packages.


In [2]:
pip install xgboost

Defaulting to user installation because normal site-packages is not writeable
     |███████████████████████████████▏| 289.5 MB 114.6 MB/s eta 0:00:01

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



     |████████████████████████████████| 36.6 MB 133.4 MB/s eta 0:00:01     |████████████████████████████████| 36.6 MB 133.4 MB/s            
     |████████████████████████████████| 18.2 MB 106.3 MB/s            
  Consider adding this directory to PATH or, if you prefer to suppress this warning, use --no-warn-script-location.
Note: you may need to restart the kernel to use updated packages.


In [2]:
pip install scikit-learn

Defaulting to user installation because normal site-packages is not writeable
     |████████████████████████████████| 10.9 MB 7.2 MB/s            
     |████████████████████████████████| 302 kB 149.3 MB/s            
Note: you may need to restart the kernel to use updated packages.


In [2]:
pip install imbalanced-learn

Defaulting to user installation because normal site-packages is not writeable
     |████████████████████████████████| 235 kB 7.1 MB/s            
Note: you may need to restart the kernel to use updated packages.


In [4]:
# Import necessary libraries and modules
from xgboost import XGBClassifier
from sklearn.model_selection import GridSearchCV
from sklearn.metrics import accuracy_score
from imblearn.over_sampling import SMOTE
from sklearn.preprocessing import LabelEncoder

In [1]:
import pandas as pd
multimodal_df1=pd.read_csv("multimodal_df.csv")

In [2]:
multimodal_df = multimodal_df1.drop("Timestamp", axis=1)

In [3]:
multimodal_df

EEG.Counter  EEG.Interpolated      EEG.AF3       EEG.F7       EEG.F3  \
0                57                 0  4316.153809  4284.102539  4248.205078   
1                58                 0  4304.871582  4277.436035  4242.820313   
2                59                 0  4311.794922  4288.589844  4250.512695   
3                60                 0  4320.512695  4289.615234  4256.153809   
4                61                 0  4313.589844  4278.589844  4246.025879   
...             ...               ...          ...          ...          ...   
770766           74                 0  4283.589844  4313.077148  4266.666504   
770767           75                 0  4269.102539  4299.871582  4262.563965   
770768           76                 0  4253.974121  4285.256348  4242.307617   
770769           77                 0  4247.051270  4283.461426  4225.256348   
770770           78                 0  4235.256348  4281.025879  4221.794922   

            EEG.FC5       EEG.T7       EEG.P7       EEG.O1       EEG.O2  \
0       4294.358887  4307.948730  4313.589844  4316.282227  4310.641113   
1       4288.205078  4289.358887  4315.769043  4317.307617  4310.256348   
2       4294.871582  4306.153809  4327.563965  4325.512695  4312.307617   
3       4297.948730  4332.563965  4327.948730  4329.230957  4314.487305   
4       4282.179688  4315.128418  4314.102539  4314.102539  4308.461426   
...             ...          ...          ...          ...          ...   
770766  4321.025879  4246.410156  4232.563965  4235.641113  4228.205078   
770767  4312.179688  4244.487305  4232.692383  4230.000000  4224.487305   
770768  4295.641113  4246.922852  4222.436035  4219.230957  4214.615234   
770769  4288.077148  4246.666504  4226.666504  4225.128418  4213.333496   
770770  4290.000000  4244.871582  4230.128418  4227.692383  4211.666504   

             EEG.P8       EEG.T8      EEG.FC6       EEG.F4       EEG.F8  \
0       4309.615234  4278.974121  4229.230957  4405.256348  4248.333496   
1       4308.461426  4270.641113  4220.000000  4400.000000  4239.358887   
2       4309.615234  4275.128418  4230.128418  4410.384766  4243.974121   
3       4311.282227  4281.410156  4236.922852  4417.820313  4251.666504   
4       4303.974121  4267.436035  4227.051270  4404.358887  4247.563965   
...             ...          ...          ...          ...          ...   
770766  4200.384766  4043.974365  4326.410156  4367.051270  4246.666504   
770767  4198.589844  4072.948730  4318.589844  4358.205078  4233.077148   
770768  4184.487305  4078.333252  4300.641113  4340.512695  4210.641113   
770769  4183.205078  4083.333252  4290.769043  4338.461426  4210.256348   
770770  4186.666504  4067.692383  4283.589844  4339.358887  4208.589844   

            EEG.AF4 LearningModality  
0       4228.974121             read  
1       4225.769043             read  
2       4240.256348             read  
3       4252.307617             read  
4       4245.641113             read  
...             ...              ...  
770766  4339.871582      kinesthetic  
770767  4324.615234      kinesthetic  
770768  4300.128418      kinesthetic  
770769  4296.666504      kinesthetic  
770770  4289.871582      kinesthetic  

[770771 rows x 17 columns]

In [8]:
class_distribution = multimodal_df["LearningModality"].value_counts()
print(class_distribution)

LearningModality
read           415366
kinesthetic    188775
video          133076
audio           33554
Name: count, dtype: int64


In [9]:
from sklearn.model_selection import train_test_split

# Separate features (X) and target variable (y)
X = multimodal_df.drop("LearningModality", axis=1)  
y = multimodal_df["LearningModality"]

In [ ]:
# Splitting the data into training- set (60% of the data), a validation set (20% of the data), and a test set (20% of the data).

In [10]:
from sklearn.model_selection import train_test_split

X_train, X_temp, y_train, y_temp = train_test_split(X, y, test_size=0.4, random_state=42, stratify=y)
X_validation, X_test, y_validation, y_test = train_test_split(X_temp, y_temp, test_size=0.5, random_state=42, stratify=y_temp)

In [11]:
#Apply label encoding to the training, validation, and testing target variable
label_encoder = LabelEncoder()
y_train_encoded = label_encoder.fit_transform(y_train)
y_validation_encoded = label_encoder.transform(y_validation)
y_test_encoded = label_encoder.transform(y_test)

In [12]:
#Apply SMOTE to the resampled training data
smote = SMOTE(random_state=42)
X_train_resampled, y_train_resampled = smote.fit_resample(X_train, y_train_encoded)

In [14]:
from xgboost import XGBClassifier
from sklearn.model_selection import RandomizedSearchCV
from scipy.stats import uniform, randint

# Define a parameter grid with hyperparameter distributions for RandomizedSearchCV
param_dist = {
    'learning_rate': uniform(0.01, 0.29),  # Uniform distribution between 0.01 and 0.3
    'max_depth': randint(3, 7),  # Random integer between 3 and 6
    'n_estimators': randint(50, 201),  # Random integer between 50 and 200
    'gamma': uniform(0, 0.3),  # Uniform distribution between 0 and 0.3
    'subsample': [0.7, 0.8, 0.9, 1.0],  # A predefined set of values
    'colsample_bytree': [0.7, 0.8, 0.9, 1.0]  # A predefined set of values
}

# Set the GPU device
params = {
    "tree_method": "gpu_hist",  # Use GPU acceleration
    "device": "cuda:0"  # Specify the GPU device (use "cuda:0" for the first GPU)
}

# Create an instance of the XGBoost classifier and passed the GPU-related parameters using **params to ensure GPU acceleration
xgb_model = XGBClassifier(objective='multi:softprob', random_state=42, **params)

# Create a RandomizedSearchCV instance to perform hyperparameter tuning
random_search = RandomizedSearchCV(
    xgb_model, param_distributions=param_dist, n_iter=50, scoring='accuracy', n_jobs=-1, cv=3, verbose=3
)

# Fit the model to the training data with SMOTE applied
random_search.fit(X_train_resampled, y_train_resampled)

# Get the best hyperparameters
best_params = random_search.best_params_
print("Best Hyperparameters:", best_params)


Fitting 3 folds for each of 50 candidates, totalling 150 fits


/home/jupyter-pvaswan/.local/lib/python3.9/site-packages/xgboost/data.py:335: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(dtype):
/home/jupyter-pvaswan/.local/lib/python3.9/site-packages/xgboost/data.py:338: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  is_categorical_dtype(dtype) or is_pa_ext_categorical_dtype(dtype)
/home/jupyter-pvaswan/.local/lib/python3.9/site-packages/xgboost/data.py:335: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(dtype):
/home/jupyter-pvaswan/.local/lib/python3.9/site-packages/xgboost/data.py:338: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  is_categorical_dtype(dtype) or i

Best Hyperparameters: {'colsample_bytree': 1.0, 'gamma': 0.11101456287096485, 'learning_rate': 0.24743678325981802, 'max_depth': 6, 'n_estimators': 148, 'subsample': 0.7}
[CV 2/3] END colsample_bytree=1.0, gamma=0.2581194276809967, learning_rate=0.20106844122515105, max_depth=6, n_estimators=127, subsample=1.0;, score=0.853 total time=  29.3s
[CV 1/3] END colsample_bytree=0.8, gamma=0.13120211493908507, learning_rate=0.2725295293924726, max_depth=4, n_estimators=103, subsample=1.0;, score=0.815 total time=  18.5s
[CV 1/3] END colsample_bytree=0.9, gamma=0.13540616104689276, learning_rate=0.10484487528364549, max_depth=5, n_estimators=56, subsample=0.9;, score=0.786 total time=  13.1s
[CV 1/3] END colsample_bytree=1.0, gamma=0.23172683424786164, learning_rate=0.03639598800017673, max_depth=3, n_estimators=156, subsample=0.8;, score=0.737 total time=  25.3s
[CV 1/3] END colsample_bytree=0.8, gamma=0.2429630010998565, learning_rate=0.0920878989385661, max_depth=3, n_estimators=54, subsamp

In [15]:
from xgboost import XGBClassifier

best_params = {
    'colsample_bytree': 1.0,
    'gamma': 0.11101456287096485,
    'learning_rate': 0.24743678325981802,
    'max_depth': 6,
    'n_estimators': 148,
    'subsample': 0.7
}

xgb_model = XGBClassifier(
    objective='multi:softprob',
    random_state=42,
    tree_method="gpu_hist",
    device="cuda:0",
    **best_params
)

# Fit the model to your training data with SMOTE applied
xgb_model.fit(X_train_resampled, y_train_resampled)


/home/jupyter-pvaswan/.local/lib/python3.9/site-packages/xgboost/data.py:335: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(dtype):
/home/jupyter-pvaswan/.local/lib/python3.9/site-packages/xgboost/data.py:338: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  is_categorical_dtype(dtype) or is_pa_ext_categorical_dtype(dtype)
/home/jupyter-pvaswan/.local/lib/python3.9/site-packages/xgboost/data.py:384: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  if is_categorical_dtype(dtype):
/home/jupyter-pvaswan/.local/lib/python3.9/site-packages/xgboost/data.py:359: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  return is_int

XGBClassifier(base_score=None, booster=None, callbacks=None,
              colsample_bylevel=None, colsample_bynode=None,
              colsample_bytree=1.0, device='cuda:0', early_stopping_rounds=None,
              enable_categorical=False, eval_metric=None, feature_types=None,
              gamma=0.11101456287096485, grow_policy=None, importance_type=None,
              interaction_constraints=None, learning_rate=0.24743678325981802,
              max_bin=None, max_cat_threshold=None, max_cat_to_onehot=None,
              max_delta_step=None, max_depth=6, max_leaves=None,
              min_child_weight=None, missing=nan, monotone_constraints=None,
              multi_strategy=None, n_estimators=148, n_jobs=None,
              num_parallel_tree=None, objective='multi:softprob', ...)

In [18]:
from sklearn.metrics import accuracy_score, classification_report, confusion_matrix
# Make predictions on the resampled training data
y_pred_resampled = xgb_model.predict(X_train_resampled)


accuracy_resampled = accuracy_score(y_train_resampled, y_pred_resampled)
print("Accuracy on Resampled Training Data:", accuracy_resampled)

/home/jupyter-pvaswan/.local/lib/python3.9/site-packages/xgboost/data.py:335: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(dtype):
/home/jupyter-pvaswan/.local/lib/python3.9/site-packages/xgboost/data.py:338: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  is_categorical_dtype(dtype) or is_pa_ext_categorical_dtype(dtype)
/home/jupyter-pvaswan/.local/lib/python3.9/site-packages/xgboost/data.py:384: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  if is_categorical_dtype(dtype):
/home/jupyter-pvaswan/.local/lib/python3.9/site-packages/xgboost/data.py:359: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  return is_int

Accuracy on Resampled Training Data: 0.8735630108458825


In [19]:
# Generate a classification report for the resampled training data
class_report_resampled = classification_report(y_train_resampled, y_pred_resampled, target_names=label_encoder.classes_)
print("Classification Report on Resampled Training Data:")
print(class_report_resampled)

Classification Report on Resampled Training Data:
              precision    recall  f1-score   support

       audio       0.88      0.97      0.92    249219
 kinesthetic       0.80      0.86      0.83    249219
        read       0.92      0.76      0.84    249219
       video       0.90      0.90      0.90    249219

    accuracy                           0.87    996876
   macro avg       0.88      0.87      0.87    996876
weighted avg       0.88      0.87      0.87    996876



In [21]:
# Fit the model to your validation data
xgb_model.fit(X_validation, y_validation_encoded)

/home/jupyter-pvaswan/.local/lib/python3.9/site-packages/xgboost/data.py:335: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(dtype):
/home/jupyter-pvaswan/.local/lib/python3.9/site-packages/xgboost/data.py:338: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  is_categorical_dtype(dtype) or is_pa_ext_categorical_dtype(dtype)
/home/jupyter-pvaswan/.local/lib/python3.9/site-packages/xgboost/data.py:384: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  if is_categorical_dtype(dtype):
/home/jupyter-pvaswan/.local/lib/python3.9/site-packages/xgboost/data.py:359: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  return is_int

XGBClassifier(base_score=None, booster=None, callbacks=None,
              colsample_bylevel=None, colsample_bynode=None,
              colsample_bytree=1.0, device='cuda:0', early_stopping_rounds=None,
              enable_categorical=False, eval_metric=None, feature_types=None,
              gamma=0.11101456287096485, grow_policy=None, importance_type=None,
              interaction_constraints=None, learning_rate=0.24743678325981802,
              max_bin=None, max_cat_threshold=None, max_cat_to_onehot=None,
              max_delta_step=None, max_depth=6, max_leaves=None,
              min_child_weight=None, missing=nan, monotone_constraints=None,
              multi_strategy=None, n_estimators=148, n_jobs=None,
              num_parallel_tree=None, objective='multi:softprob', ...)

In [22]:
# Make predictions on the validation data
y_pred_validation = xgb_model.predict(X_validation)

/home/jupyter-pvaswan/.local/lib/python3.9/site-packages/xgboost/data.py:335: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(dtype):
/home/jupyter-pvaswan/.local/lib/python3.9/site-packages/xgboost/data.py:338: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  is_categorical_dtype(dtype) or is_pa_ext_categorical_dtype(dtype)
/home/jupyter-pvaswan/.local/lib/python3.9/site-packages/xgboost/data.py:384: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  if is_categorical_dtype(dtype):
/home/jupyter-pvaswan/.local/lib/python3.9/site-packages/xgboost/data.py:359: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  return is_int

In [23]:
# Calculate the accuracy on the validation data
accuracy_validation = accuracy_score(y_validation_encoded, y_pred_validation)
print("Accuracy on Validation Data:", accuracy_validation)

Accuracy on Validation Data: 0.8876448227097578


In [24]:
# Generate a classification report for the validation data
class_report_validation = classification_report(y_validation_encoded, y_pred_validation, target_names=label_encoder.classes_)
print("Classification Report on Validation Data:")
print(class_report_validation)

Classification Report on Validation Data:
              precision    recall  f1-score   support

       audio       0.88      0.67      0.77      6711
 kinesthetic       0.83      0.84      0.83     37755
        read       0.90      0.94      0.92     83073
       video       0.94      0.85      0.89     26615

    accuracy                           0.89    154154
   macro avg       0.89      0.83      0.85    154154
weighted avg       0.89      0.89      0.89    154154



In [26]:
y_pred_test = xgb_model.predict(X_test)

/home/jupyter-pvaswan/.local/lib/python3.9/site-packages/xgboost/data.py:335: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(dtype):
/home/jupyter-pvaswan/.local/lib/python3.9/site-packages/xgboost/data.py:338: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  is_categorical_dtype(dtype) or is_pa_ext_categorical_dtype(dtype)
/home/jupyter-pvaswan/.local/lib/python3.9/site-packages/xgboost/data.py:384: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  if is_categorical_dtype(dtype):
/home/jupyter-pvaswan/.local/lib/python3.9/site-packages/xgboost/data.py:359: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  return is_int

In [27]:
# Calculate the accuracy on the test data
accuracy_test = accuracy_score(y_test_encoded, y_pred_test)
print("Accuracy on Test Data:", accuracy_test)

Accuracy on Test Data: 0.8434303136453569


In [28]:
# Generate a classification report for the test data
class_report_test = classification_report(y_test_encoded, y_pred_test, target_names=label_encoder.classes_)
print("Classification Report on Test Data:")
print(class_report_test)

Classification Report on Test Data:
              precision    recall  f1-score   support

       audio       0.74      0.49      0.59      6711
 kinesthetic       0.77      0.79      0.78     37755
        read       0.87      0.91      0.89     83074
       video       0.90      0.80      0.85     26615

    accuracy                           0.84    154155
   macro avg       0.82      0.75      0.78    154155
weighted avg       0.84      0.84      0.84    154155



In [13]:
from xgboost import XGBClassifier
from sklearn.model_selection import GridSearchCV

# Define a parameter grid with hyperparameter values for XGBoost
param_grid = {
    'learning_rate': [0.01, 0.1, 0.2, 0.3],
    'max_depth': [3, 4, 5, 6],
    'n_estimators': [50, 100, 150, 200],
    'gamma': [0, 0.1, 0.2, 0.3],
    'subsample': [0.7, 0.8, 0.9, 1.0],
    'colsample_bytree': [0.7, 0.8, 0.9, 1.0],
}

# Set the GPU device
params = {
    "tree_method": "gpu_hist",  # Use GPU acceleration
    "device": "cuda:0"  # Specify the GPU device (use "cuda:0" for the first GPU)
}

# Create an instance of the XGBoost classifier with GPU acceleration
xgb_model = XGBClassifier(objective='multi:softprob', random_state=42, **params)

# Create a GridSearchCV instance to perform hyperparameter tuning
grid_search = GridSearchCV(
    xgb_model, param_grid=param_grid, scoring='accuracy', n_jobs=-1, cv=3, verbose=3
)

# Fit the model to the training data with SMOTE applied
grid_search.fit(X_train_resampled, y_train_resampled)

# Get the best hyperparameters
best_params = grid_search.best_params_
print("Best Hyperparameters:", best_params)




Fitting 3 folds for each of 4096 candidates, totalling 12288 fits


/home/jupyter-pvaswan/.local/lib/python3.9/site-packages/xgboost/data.py:335: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(dtype):
/home/jupyter-pvaswan/.local/lib/python3.9/site-packages/xgboost/data.py:335: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(dtype):
/home/jupyter-pvaswan/.local/lib/python3.9/site-packages/xgboost/data.py:335: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(dtype):
/home/jupyter-pvaswan/.local/lib/python3.9/site-packages/xgboost/data.py:338: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  is_categorical_dtype(dtype) or is_pa_ext_categorical_dtype(dtype)
/home/jupyter-pvasw

[CV 2/3] END colsample_bytree=0.7, gamma=0, learning_rate=0.01, max_depth=3, n_estimators=50, subsample=1.0;, score=0.671 total time=  10.3s
[CV 2/3] END colsample_bytree=0.7, gamma=0, learning_rate=0.01, max_depth=3, n_estimators=100, subsample=0.7;, score=0.677 total time=  15.6s
[CV 1/3] END colsample_bytree=0.7, gamma=0, learning_rate=0.01, max_depth=3, n_estimators=150, subsample=0.7;, score=0.684 total time=  19.5s
[CV 1/3] END colsample_bytree=0.7, gamma=0, learning_rate=0.01, max_depth=3, n_estimators=200, subsample=0.7;, score=0.692 total time=  20.4s
[CV 1/3] END colsample_bytree=0.7, gamma=0, learning_rate=0.01, max_depth=4, n_estimators=50, subsample=0.7;, score=0.710 total time=  10.1s
[CV 2/3] END colsample_bytree=0.7, gamma=0, learning_rate=0.01, max_depth=4, n_estimators=50, subsample=0.7;, score=0.712 total time=   5.5s
[CV 2/3] END colsample_bytree=0.7, gamma=0, learning_rate=0.01, max_depth=4, n_estimators=100, subsample=0.7;, score=0.716 total time=  15.9s


/home/jupyter-pvaswan/.local/lib/python3.9/site-packages/joblib/externals/loky/process_executor.py:752: UserWarning: A worker stopped while some jobs were given to the executor. This can be caused by a too short worker timeout or by a memory leak.
  warnings.warn(
/home/jupyter-pvaswan/.local/lib/python3.9/site-packages/xgboost/core.py:160: UserWarning: [11:53:19] WARNING: /workspace/src/common/error_msg.cc:27: The tree method `gpu_hist` is deprecated since 2.0.0. To use GPU training, set the `device` parameter to CUDA instead.

    E.g. tree_method = "hist", device = "cuda"

  warnings.warn(smsg, UserWarning)
/home/jupyter-pvaswan/.local/lib/python3.9/site-packages/xgboost/data.py:335: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(dtype):
/home/jupyter-pvaswan/.local/lib/python3.9/site-packages/xgboost/data.py:338: FutureWarning: is_categorical_dtype is deprecated and will be removed in

[CV 3/3] END colsample_bytree=0.7, gamma=0, learning_rate=0.01, max_depth=3, n_estimators=50, subsample=0.7;, score=0.672 total time=  10.6s
[CV 2/3] END colsample_bytree=0.7, gamma=0, learning_rate=0.01, max_depth=3, n_estimators=100, subsample=0.9;, score=0.677 total time=  16.1s
[CV 2/3] END colsample_bytree=0.7, gamma=0, learning_rate=0.01, max_depth=3, n_estimators=150, subsample=0.9;, score=0.683 total time=  23.3s
[CV 2/3] END colsample_bytree=0.7, gamma=0, learning_rate=0.01, max_depth=3, n_estimators=200, subsample=1.0;, score=0.690 total time=  29.9s
[CV 2/3] END colsample_bytree=0.7, gamma=0, learning_rate=0.01, max_depth=4, n_estimators=50, subsample=0.8;, score=0.712 total time=   9.9s
[CV 2/3] END colsample_bytree=0.7, gamma=0, learning_rate=0.01, max_depth=4, n_estimators=100, subsample=0.8;, score=0.718 total time=  18.0s
[CV 2/3] END colsample_bytree=0.7, gamma=0, learning_rate=0.01, max_depth=4, n_estimators=150, subsample=0.8;, score=0.725 total time=  26.8s


...

[CV 1/3] END colsample_bytree=0.7, gamma=0.3, learning_rate=0.3, max_depth=3, n_estimators=50, subsample=0.9;, score=0.770 total time=   5.5s
[CV 1/3] END colsample_bytree=0.7, gamma=0.3, learning_rate=0.3, max_depth=3, n_estimators=100, subsample=0.9;, score=0.795 total time=  15.4s
[CV 1/3] END colsample_bytree=0.7, gamma=0.3, learning_rate=0.3, max_depth=3, n_estimators=150, subsample=0.9;, score=0.806 total time=  23.3s
[CV 1/3] END colsample_bytree=0.7, gamma=0.3, learning_rate=0.3, max_depth=3, n_estimators=200, subsample=0.9;, score=0.813 total time=  30.8s
[CV 1/3] END colsample_bytree=0.7, gamma=0.3, learning_rate=0.3, max_depth=4, n_estimators=50, subsample=0.9;, score=0.796 total time=   9.6s
[CV 1/3] END colsample_bytree=0.7, gamma=0.3, learning_rate=0.3, max_depth=4, n_estimators=100, subsample=0.9;, score=0.817 total time=  18.7s
[CV 1/3] END colsample_bytree=0.7, gamma=0.3, learning_rate=0.3, max_depth=4, n_estimators=150, subsample=0.9;, score=0.828 total time=  27.5s
[

/home/jupyter-pvaswan/.local/lib/python3.9/site-packages/xgboost/data.py:335: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(dtype):
/home/jupyter-pvaswan/.local/lib/python3.9/site-packages/xgboost/data.py:338: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  is_categorical_dtype(dtype) or is_pa_ext_categorical_dtype(dtype)
/home/jupyter-pvaswan/.local/lib/python3.9/site-packages/xgboost/data.py:384: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  if is_categorical_dtype(dtype):
/home/jupyter-pvaswan/.local/lib/python3.9/site-packages/xgboost/data.py:359: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  return is_int

[CV 3/3] END colsample_bytree=0.7, gamma=0.3, learning_rate=0.3, max_depth=3, n_estimators=100, subsample=0.9;, score=0.798 total time=  15.1s
[CV 1/3] END colsample_bytree=0.7, gamma=0.3, learning_rate=0.3, max_depth=3, n_estimators=150, subsample=1.0;, score=0.806 total time=  21.7s
[CV 3/3] END colsample_bytree=0.7, gamma=0.3, learning_rate=0.3, max_depth=3, n_estimators=200, subsample=0.9;, score=0.818 total time=  29.8s
[CV 2/3] END colsample_bytree=0.7, gamma=0.3, learning_rate=0.3, max_depth=4, n_estimators=50, subsample=1.0;, score=0.798 total time=   9.1s
[CV 3/3] END colsample_bytree=0.7, gamma=0.3, learning_rate=0.3, max_depth=4, n_estimators=100, subsample=0.9;, score=0.821 total time=  18.5s
[CV 3/3] END colsample_bytree=0.7, gamma=0.3, learning_rate=0.3, max_depth=4, n_estimators=150, subsample=1.0;, score=0.834 total time=  26.9s
[CV 2/3] END colsample_bytree=0.7, gamma=0.3, learning_rate=0.3, max_depth=4, n_estimators=200, subsample=0.9;, score=0.841 total time=  36.5s


/home/jupyter-pvaswan/.local/lib/python3.9/site-packages/xgboost/data.py:335: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(dtype):
/home/jupyter-pvaswan/.local/lib/python3.9/site-packages/xgboost/data.py:338: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  is_categorical_dtype(dtype) or is_pa_ext_categorical_dtype(dtype)
/home/jupyter-pvaswan/.local/lib/python3.9/site-packages/xgboost/data.py:384: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  if is_categorical_dtype(dtype):
/home/jupyter-pvaswan/.local/lib/python3.9/site-packages/xgboost/data.py:359: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  return is_int

KeyboardInterrupt: 